# Oberflächentemperatur (Land Surface Temperature)

## Authentifizierung

In [16]:
import openeo

connection = openeo.connect("https://openeo.dataspace.copernicus.eu/").authenticate_oidc()

Visit https://identity.dataspace.copernicus.eu/auth/realms/CDSE/device?user_code=QHKA-VXMK 📋 to authenticate.

✅ Authorized successfully

Authenticated using device code flow.


## Verwaltungsgrenzen von Bremen

In [19]:
import geopandas as gpd

gdf = gpd.read_file('Verwaltungsgrenzen_HB_BHV', layer="hb_landesflaeche_Teil_I_BRE")
gdf

id bez_lan   sch_lan repentuncd unaggid agglomerat  inhabitant        size  \
0   1  Bremen  04000000       None    None       None         NaN  318.195497   

                                            geometry  
0  MULTIPOLYGON (((474358.64 5894064.42, 474311.0...

In [22]:
gdf.explore()

## Räumliche Ausdehnung

Bestimmung der räumlichen Ausdehnung anhand der Vektorgeometrien

In [23]:
# Bounding Box bestimmen
bbox = gdf.to_crs('WGS84').total_bounds.tolist()
bbox

[8.481758449250766, 53.01115244699335, 8.990813245344944, 53.2289106605276]

In [ ]:
spatial_extent=dict(zip(["west", "south", "east", "north"], bbox))

spatial_extent

spatial_extent = {'west': 8.721771, 'south': 53.025027, 'east': 8.904419, 'north': 53.114965}

{'west': 8.481758449250766,
 'south': 53.01115244699335,
 'east': 8.990813245344944,
 'north': 53.2289106605276}

## Zeitliche Ausdehnung

In [25]:
temporal_extent = ["2024-06-01", "2024-08-31"]

In [26]:
cube = connection.load_collection(
    "SENTINEL3_SLSTR_L2_LST",
    spatial_extent=spatial_extent,
    temporal_extent=temporal_extent,
    bands=["LST"]
)


cube = cube.mean_time()

lst = cube.save_result(format="GTIFF")
job = lst.create_job(title="LST")
job.start_and_wait().download_result('results/lst.tif')

0:00:00 Job 'j-2510111146024febaf1f1d58a9a115af': send 'start'
0:00:13 Job 'j-2510111146024febaf1f1d58a9a115af': created (progress 0%)
0:00:18 Job 'j-2510111146024febaf1f1d58a9a115af': created (progress 0%)
0:00:24 Job 'j-2510111146024febaf1f1d58a9a115af': created (progress 0%)
0:00:32 Job 'j-2510111146024febaf1f1d58a9a115af': created (progress 0%)
0:00:42 Job 'j-2510111146024febaf1f1d58a9a115af': created (progress 0%)
0:00:55 Job 'j-2510111146024febaf1f1d58a9a115af': created (progress 0%)
0:01:10 Job 'j-2510111146024febaf1f1d58a9a115af': running (progress N/A)
0:01:29 Job 'j-2510111146024febaf1f1d58a9a115af': running (progress N/A)
0:01:53 Job 'j-2510111146024febaf1f1d58a9a115af': running (progress N/A)
0:02:23 Job 'j-2510111146024febaf1f1d58a9a115af': running (progress N/A)
0:03:00 Job 'j-2510111146024febaf1f1d58a9a115af': running (progress N/A)
0:03:47 Job 'j-2510111146024febaf1f1d58a9a115af': finished (progress 100%)


PosixPath('results/lst.tif')

In [1]:
import leafmap

m = leafmap.Map()

m.add_raster(
    'results/lst.tif',
    cmap="coolwarm",
    layer_name="Land Surface Temperature"
)

m

Map(center=[53.1173035, 8.740687], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title',…

In [36]:
import rasterio as rio

src = rio.open('results/lst.tif')

In [37]:
# Temperatur von Kelvin in Celsius umrechnen
lst = src.read() - 272.15

In [38]:
import plotly.express as px

px.imshow(
    lst[0],
    color_continuous_scale='thermal',
    #zmin=5,
    #zmax=12
)

ValueError: Mime type rendering requires nbformat>=4.2.0 but it is not installed

Figure({
    'data': [{'coloraxis': 'coloraxis',
              'hovertemplate': 'x: %{x}<br>y: %{y}<br>color: %{z}<extra></extra>',
              'name': '0',
              'type': 'heatmap',
              'xaxis': 'x',
              'yaxis': 'y',
              'z': {'bdata': ('gIXtQEA3+UCgiQxBwH4QQeB4DkFAJw' ... 'FAhAlBICoJQYDzBUHAw/9AwED/QA=='),
                    'dtype': 'f4',
                    'shape': '25, 58'}}],
    'layout': {'coloraxis': {'colorscale': [[0.0, 'rgb(3, 35, 51)'],
                                            [0.09090909090909091, 'rgb(13, 48,
                                            100)'], [0.18181818181818182, 'rgb(53,
                                            50, 155)'], [0.2727272727272727,
                                            'rgb(93, 62, 153)'],
                                            [0.36363636363636365, 'rgb(126, 77,
                                            143)'], [0.45454545454545453, 'rgb(158,
                                            89, 135)'], [0.5454545454545454,
                                            'rgb(193, 100, 121)'],
                                            [0.6363636363636364, 'rgb(225, 113,
                                            97)'], [0.7272727272727273, 'rgb(246,
                                            139, 69)'], [0.8181818181818182,
                                            'rgb(251, 173, 60)'],
                                            [0.9090909090909091, 'rgb(246, 211,
                                            70)'], [1.0, 'rgb(231, 250, 90)']]},
               'margin': {'t': 60},
               'template': '...',
               'xaxis': {'anchor': 'y', 'constrain': 'domain', 'domain': [0.0, 1.0], 'scaleanchor': 'y'},
               'yaxis': {'anchor': 'x', 'autorange': 'reversed', 'constrain': 'domain', 'domain': [0.0, 1.0]}}
})